In [1]:
import pandas as pd
import numpy as np
import spacy
nlp = spacy.load("en_core_web_sm")

In [72]:
import pyreadr
rfile = pyreadr.read_r('../input/cleaned_comment_text.RDS')
dt = rfile[None]
rfile2 = pyreadr.read_r('../input/cleaned_comment_meta.RDS')
meta = rfile2[None]
form_letter = pd.read_table('../input/form_letter_designation.txt')
nonform = form_letter['UQID'][form_letter['FORM']==0]
dt = dt[pd.to_numeric(dt.UQID).isin(nonform)]
meta = meta[pd.to_numeric(meta.UQID).isin(nonform)]
### this is just for testing
#45579
meta = meta[meta['Project.Number']=='45579']
dt = dt[pd.to_numeric(dt.UQID).isin(pd.to_numeric(meta.UQID))]

/opt/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3251: DtypeWarning: Columns (2) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [73]:
dt = dt[pd.to_numeric(dt.UQID).isin(nonform)]
meta = meta[pd.to_numeric(meta.UQID).isin(nonform)]


In [82]:
tokenized = [nlp(t) for t in dt['Letter.Text.Clean']]

NameError: name 'text' is not defined

NameError: name 'text' is not defined

In [85]:
import spacy
from spacy.matcher import Matcher
nlp = spacy.load("en_core_web_sm")
matcher = Matcher(nlp.vocab)

#pass1 = [{"TEXT": {"REGEX": "(is|was)"}}, {"POS": "ADV", "OP": "*"}, {"TAG": "VBN"}
#pass2 = [{"LEMMA": "have"}, {"TEXT":"been"}, {"POS": "ADV", "OP": "*"}, {"TAG": "VBN"}]
#matcher.add("pass1", None, pass1)
#matcher.add("pass2", None, pass2)

In [83]:
vocab = {"<UNK>": 1, "<PAD>": 0}
for txt in tokenized:
    for token in txt:
        if token.text not in vocab.keys():
            vocab[token.text] = len(vocab)
print("Number of unique tokens: {}".format(len(vocab)))

Number of unique tokens: 18184


In [43]:
import nltk
test = dt['Letter.Text.Clean'][35]
sentList = nltk.sent_tokenize(test) # Splitting the text into sentences


In [66]:

for sentence in sentList:
  doc = nlp(sentence)
  for token in doc:
    print(token.text, token.dep_, token.head.text, token.head.pos_,
      token.pos_,[child for child in token.children])

Forest compound fires NOUN NOUN []
fires nsubjpass used VERB NOUN [Forest]
should aux used VERB AUX []
not neg used VERB PART []
be auxpass used VERB AUX []
used ROOT used VERB VERB [fires, should, not, be, as, .]
as prep used VERB ADP [excuse]
an det excuse NOUN DET []
excuse pobj as ADP NOUN [an, ignore]
to aux ignore VERB PART []
ignore acl excuse NOUN VERB [to, science, and, shut]
science dobj ignore VERB NOUN []
and cc ignore VERB CCONJ []
shut conj ignore VERB VERB [out, public]
out prt shut VERB ADP []
the det public NOUN DET []
public dobj shut VERB NOUN [the]
. punct used VERB PUNCT []


In [46]:
for sentence in sentList:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  print(sentence)
  print(descriptive_term)

Please say No  toEmergency Declaration for Klamath Please  protect and save our precious wild forests (public lands ) and watersheds of the Klamath Forest from destruction.
public
For years I have traveled to the west north in small pilot plane to see my family.
small
I have seen the destruction of mass logging and of our beautiful forest it makes my skin crawl that we don't have respect for  Mother natures glories.
beautiful
Forest fires should not be used as an excuse to ignore science and shut out the public.

It should be a crime once it's gone it's gone.

I shutter to think of Old-growth reserves wiped out.
Old
Now is the time for the Klamath National Forest to work with the public and scientists to recover, rather than exploit, forests that belong to all Americans.

Please reject the request of the Klamath National Forest to begin clear cutting these forests prior to any meaningful review process.
meaningful


In [70]:

sentList = [
  'The food we had yesterday was delicious',
  'My time in Italy was very enjoyable',
  'I found the meal to be tasty',
  'The internet was slow.',
  'Our experience was suboptimal'
]
sentList = ['Forest fires should not be used as an excuse to ignore science and shut out the public.']
for sentence in sentList:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      descriptive_term = token
  print(sentence)
  print(descriptive_term)

Forest fires should not be used as an excuse to ignore science and shut out the public.



In [71]:
aspects = []
for sentence in sentList:
  doc = nlp(sentence)
  descriptive_term = ''
  target = ''
  for token in doc:
    if (token.dep_ == 'nsubj' or token.dep == 'nsubjpass') and token.pos_ == 'NOUN':
      target = token.text
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  aspects.append({'aspect': target,
    'description': descriptive_term})
print(aspects)

[{'aspect': '', 'description': ''}]


In [72]:

for sentence in sentList:
  doc = nlp(sentence)
  for token in doc:
    print(token.text, token.dep_, token.head.text, token.head.pos_,
      token.pos_,[child for child in token.children])

Forest compound fires NOUN NOUN []
fires nsubjpass used VERB NOUN [Forest]
should aux used VERB AUX []
not neg used VERB PART []
be auxpass used VERB AUX []
used ROOT used VERB VERB [fires, should, not, be, as, .]
as prep used VERB ADP [excuse]
an det excuse NOUN DET []
excuse pobj as ADP NOUN [an, ignore]
to aux ignore VERB PART []
ignore acl excuse NOUN VERB [to, science, and, shut]
science dobj ignore VERB NOUN []
and cc ignore VERB CCONJ []
shut conj ignore VERB VERB [out, public]
out prt shut VERB ADP []
the det public NOUN DET []
public dobj shut VERB NOUN [the]
. punct used VERB PUNCT []


In [73]:
from textblob import TextBlob
for aspect in aspects:
  aspect['sentiment'] = TextBlob(aspect['description']).sentiment
print(aspects)

[{'aspect': '', 'description': '', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}]


In [78]:
import os
from pandas import read_csv
from numpy import random

Sentiment(polarity=-0.025, subjectivity=0.058333333333333334)

In [55]:
aspects[0]

{'aspect': '',
 'description': 'public',
 'sentiment': Sentiment(polarity=0.0, subjectivity=0.06666666666666667)}

In [6]:
nlp = stanza.Pipeline('en') # initialize English neural pipeline
#nlp = stanfordnlp.Pipeline()

2022-03-24 22:53:38 INFO: Loading these models for language: en (English):
| Processor    | Package   |
----------------------------
| tokenize     | combined  |
| pos          | combined  |
| lemma        | combined  |
| depparse     | combined  |
| sentiment    | sstplus   |
| constituency | wsj       |
| ner          | ontonotes |

2022-03-24 22:53:38 INFO: Use device: cpu
2022-03-24 22:53:38 INFO: Loading: tokenize
2022-03-24 22:53:38 INFO: Loading: pos
2022-03-24 22:53:38 INFO: Loading: lemma
2022-03-24 22:53:38 INFO: Loading: depparse
2022-03-24 22:53:38 INFO: Loading: sentiment
2022-03-24 22:53:38 INFO: Loading: constituency
2022-03-24 22:53:39 INFO: Loading: ner
2022-03-24 22:53:39 INFO: Done loading processors!


In [27]:
stop_words = set(stopwords.words('english'))
txt = dt['Letter.Text.Clean'][0]

In [48]:
txt2 = txt[:1000]

In [49]:
res = (aspect_sentiment_analysis(txt2, stop_words, nlp))

# Output: [['soundquality', ['great']], ['batterylife', ['bad']]]

In [51]:
[a[1] for a in res]

[[],
 ['grant'],
 ['fires'],
 ['ignore'],
 ['to'],
 ['a'],
 ['salmon'],
 ['it'],
 [],
 ['forests'],
 [],
 ['clear', 'cutting'],
 ['begin', 'forests'],
 ['meaningful'],
 [],
 ['goosenest', 'shown'],
 ['forest', 'forests'],
 ['forests'],
 ['values'],
 [],
 ['massive']]

In [52]:
res

[['please', []],
 ['emergencydeclaration', ['grant']],
 ['forest', ['fires']],
 ['science', ['ignore']],
 ['salvage', ['to']],
 ['proposal', ['a']],
 ['recovery', ['salmon']],
 ['time', ['it']],
 ['work', []],
 ['exploit', ['forests']],
 ['please', []],
 ['begin', ['clear', 'cutting']],
 ['cutting', ['begin', 'forests']],
 ['reviewprocess', ['meaningful']],
 ['note', []],
 ['rangerdistrict', ['goosenest', 'shown']],
 ['manage', ['forest', 'forests']],
 ['post-fire', ['forests']],
 ['conservation', ['values']],
 ['nation', []],
 ['west', ['massive']]]

In [40]:
txt2

'Please do not grant Emergency Declaration for Klamath Forest fires should not be used as an excuse to ignore science and shut out the public. It is my understanding that the Klamath National Forest is fast-tracking a massive salvage clear cutting proposal to convert thousands of acres of public lands into fiber plantations.'

In [1]:
# We get started by importing spacy
import spacy
nlp = spacy.load("en_core_web_sm")


In [2]:
import pandas as pd
df = pd.read_csv('../input/')

In [3]:
df_meta = pd.read_csv('../scratch/cleaned_comment_meta.txt')

In [7]:
df2 = df[df['Letter.Text.Clean'].isna() == False]

In [55]:
toks = [sent_tokenize(d) for d in df2['Letter.Text.Clean'][:n]]

In [62]:
tok_all = [item for sublist in toks for item in sublist]

In [98]:
from textblob.sentiments import NaiveBayesAnalyzer


In [120]:
for s in blob.sentences:
    print(s)
    print(s.sentiment)

visiting from las vegas.
Sentiment(classification='pos', p_pos=0.5433944820530477, p_neg=0.4566055179469529)
here for the mountain biking.
Sentiment(classification='neg', p_pos=0.4837047587495006, p_neg=0.5162952412504997)
having the may valley trails as an option to ride in addition to the idyllwild trails was a perfect fit for my  day visit.
Sentiment(classification='pos', p_pos=0.9084917625415535, p_neg=0.09150823745844569)
i would love to share these trails with all of my friends in las vegas.
Sentiment(classification='pos', p_pos=0.6493165198504844, p_neg=0.3506834801495147)
please keep the current may valley trails open.
Sentiment(classification='neg', p_pos=0.43611893860571743, p_neg=0.5638810613942836)


In [ ]:
sents = []
for com in df2['Letter.Text.Clean']:
    blob = TextBlob(test,analyzer=NaiveBayesAnalyzer())
    sents.append(blob.sentiment)

In [111]:

for sentence in blob.sentences:
    st.append([str(sentence),sentence.polarity, sentence.subjectivity,sentence.sentiment.classification])
print(st)

[['visiting from las vegas.here for the mountain biking.having the may valley trails as an option to ride in addition to the idyllwild trails was a perfect fit for my  day visit.i would love to share these trails with all of my friends in las vegas.please keep the current may valley trails open.shastatrinity national forest httpwww.fs.usda.govstnf  i am a frequent user of the hurkey, may valley, and southridge area trails, and appreciate the value the nfs places on the trail system there, and the emphasis on legitimizing these truly amazing trails by affording them official nfs trail status.that is great news i have read the may th usfs letter with proposed management and trail closures.many of these proposed trail closures make some sense, but many do not.some of the core mid may valley technical trails like log pile, uno and tres hombres, and secret being considered for closure are sacred trails to the mountain biking community in my opinion.please please do not close these trails .'

In [64]:
for sentence in tok_all:
  doc = nlp(sentence)
  for token in doc:
    print(token.text, token.dep_, token.head.text, token.head.pos_,
      token.pos_,[child for child in token.children])


visiting ROOT visiting VERB VERB [from, .]
from prep visiting VERB ADP [vegas]
las compound vegas PROPN PROPN []
vegas pobj from ADP PROPN [las]
. punct visiting VERB PUNCT []
here ROOT here ADV ADV [for, .]
for prep here ADV ADP [biking]
the det biking NOUN DET []
mountain compound biking NOUN NOUN []
biking pobj for ADP NOUN [the, mountain]
. punct here ADV PUNCT []
having csubj was AUX VERB [trails, as]
the det trails NOUN DET []
may compound valley PROPN PROPN []
valley compound trails NOUN PROPN [may]
trails dobj having VERB NOUN [the, valley]
as prep having VERB ADP [option]
an det option NOUN DET []
option pobj as ADP NOUN [an, ride]
to aux ride VERB PART []
ride acl option NOUN VERB [to, in]
in prep ride VERB ADP [addition]
addition pobj in ADP NOUN [to]
to prep addition NOUN ADP [trails]
the det trails NOUN DET []
idyllwild amod trails NOUN ADJ []
trails pobj to ADP NOUN [the, idyllwild]
was ROOT was AUX AUX [having, fit, .]
a det fit NOUN DET []
perfect amod fit NOUN ADJ []
f

a det descent NOUN DET []
fun amod descent NOUN NOUN []
descent conj climb NOUN NOUN [a, fun]
, punct is AUX PUNCT []
and cc is AUX CCONJ []
has conj is AUX VERB [number, ,, and, reminds]
a det number NOUN DET []
number dobj has VERB NOUN [a, of]
of prep number NOUN ADP [sections]
challenging amod sections NOUN ADJ []
sections pobj of ADP NOUN [challenging, are]
that nsubj are AUX PRON []
are relcl sections NOUN AUX [that, rewarding]
very advmod rewarding ADJ ADV []
rewarding acomp are AUX ADJ [very, ride]
to aux ride VERB PART []
ride xcomp rewarding ADJ VERB [to]
, punct has VERB PUNCT []
and cc has VERB CCONJ []
the det section NOUN DET []
bottom amod section NOUN ADJ []
section nsubj reminds VERB NOUN [the, bottom, through]
through prep section NOUN ADP [pines]
the det pines NOUN DET []
pines pobj through ADP NOUN [the, and, straw]
and cc pines NOUN CCONJ []
pine amod straw NOUN ADJ []
straw conj pines NOUN NOUN [pine]
reminds conj has VERB VERB [section, me, of]
me dobj reminds VE

if mark are AUX SCONJ []
you nsubj are AUX PRON []
are advcl note VERB AUX [if, you,  ]
  dep are AUX SPACE [not, recipient]
not neg   SPACE PART []
the det recipient NOUN DET []
intended amod recipient NOUN VERB []
recipient appos   SPACE NOUN [the, intended]
please intj note VERB INTJ []
note ROOT note VERB VERB [are, please, prohibited, .]
that mark prohibited VERB SCONJ []
any det disclosure NOUN DET []
disclosure nsubjpass prohibited VERB NOUN [any, ,, distribution]
, punct disclosure NOUN PUNCT []
  dep distribution NOUN SPACE []
distribution appos disclosure NOUN NOUN [ , ,, or, copying]
, punct distribution NOUN PUNCT []
or cc distribution NOUN CCONJ []
copying conj distribution NOUN NOUN [of]
of prep copying NOUN ADP [email]
this det email NOUN DET []
email pobj of ADP NOUN [this]
is auxpass prohibited VERB AUX []
strictly advmod prohibited VERB ADV []
prohibited ccomp note VERB VERB [that, disclosure, is, strictly, and, be]
and cc prohibited VERB CCONJ []
may aux be AUX AUX [

a det lot NOUN DET []
lot nsubj are AUX NOUN [a, of]
of prep lot NOUN ADP [trails]
these det trails NOUN DET []
trails pobj of ADP NOUN [these]
are ROOT are AUX AUX [lot, at, and, get, .]
at prep are AUX ADP [point]
the det point NOUN DET []
further amod point NOUN ADV []
most amod point NOUN ADJ []
point pobj at ADP NOUN [the, further, most, from]
from prep point NOUN ADP [alley]
either preconj alley NOUN CCONJ []
trail compound head NOUN NOUN []
head compound alley NOUN NOUN [trail]
cowbell compound alley NOUN NOUN []
alley pobj from ADP NOUN [either, head, cowbell, or, creek]
or cc alley NOUN CCONJ []
hurkey compound creek NOUN NOUN []
creek conj alley NOUN NOUN [hurkey]
and cc are AUX CCONJ []
therefore advmod get VERB ADV []
get conj are AUX VERB [therefore, traffic]
little amod beginner NOUN ADJ []
beginner compound traffic NOUN NOUN [little]
traffic dobj get VERB NOUN [beginner]
. punct are AUX PUNCT []
as mark stated VERB SCONJ []
stated ROOT stated VERB VERB [as, is, .]
before

the det substrate NOUN DET []
dry amod substrate NOUN ADJ []
sandy amod substrate NOUN ADJ []
substrate nsubj are AUX NOUN [the, dry, sandy, ,, interspersed]
, punct substrate NOUN PUNCT []
interspersed acl substrate NOUN VERB [with]
with prep interspersed VERB ADP [features]
massive amod features NOUN ADJ []
rock compound features NOUN NOUN []
features pobj with ADP NOUN [massive, rock]
are ROOT are AUX AUX [substrate, unmatched, .]
unmatched acomp are AUX ADJ [else, ridden]
anywhere advmod else ADV ADV []
else advmod unmatched ADJ ADV [anywhere]
i nsubj ridden VERB PRON []
ve aux ridden VERB AUX []
ridden ccomp unmatched ADJ VERB [i, ve, in]
in prep ridden VERB ADP [socal]
socal pobj in ADP ADJ []
. punct are AUX PUNCT []
these det trails NOUN DET []
trails nsubj offer VERB NOUN [these]
offer ROOT offer VERB VERB [trails, style, .]
a det style NOUN DET []
unique amod style NOUN ADJ []
style dobj offer VERB NOUN [a, unique, of, ,, interspersed]
of prep style NOUN ADP [riding]
riding p

...

the det service NOUN DET []
forest compound service NOUN NOUN []
service nsubj ensure VERB NOUN [the, forest]
should aux ensure VERB AUX []
ensure ROOT ensure VERB VERB [service, should, used, .]
that mark used VERB SCONJ []
public amod lands NOUN ADJ []
lands nsubjpass used VERB NOUN [public]
are auxpass used VERB AUX []
not neg used VERB PART []
used ccomp ensure VERB VERB [that, lands, are, not, for]
for prep used VERB ADP [mt]
mining compound mt PROPN NOUN []
mt pobj for ADP PROPN [mining]
. punct ensure VERB PUNCT []
taylor compound   SPACE PROPN []
  dep   SPACE SPACE [taylor, sacred, .]
sacred amod   SPACE ADJ [to]
to prep sacred ADJ ADP [tribes]
native amod tribes NOUN ADJ []
tribes pobj to ADP NOUN [native, ,, precious]
, punct tribes NOUN PUNCT []
precious amod tribes NOUN ADJ [for, in]
for prep precious ADJ ADP [groundwater]
groundwater pobj for ADP NOUN []
in prep precious ADJ ADP [land]
an det land NOUN DET []
arid amod land NOUN ADJ []
land pobj in ADP NOUN [an, arid]
. p

mining compound shafts NOUN NOUN []
shafts dobj prohibit VERB NOUN [mining, on]
on prep shafts NOUN ADP [lands]
lands pobj on ADP NOUN [held]
held acl lands NOUN VERB [in]
in prep held VERB ADP [trust]
trust pobj in ADP NOUN [for]
for prep trust NOUN ADP [americans]
all det americans NOUN DET []
americans pobj for ADP NOUN [all, ,, present]
, punct americans NOUN PUNCT []
present amod americans NOUN ADJ [and, future]
and cc present ADJ CCONJ []
future conj present ADJ ADJ []
. punct urge VERB PUNCT []
in prep identify VERB ADP [addition]
addition pobj in ADP NOUN [to]
to prep addition NOUN ADP [encroaching]
encroaching pcomp to ADP VERB [on]
on prep encroaching VERB ADP [lands]
sacred amod lands NOUN ADJ []
lands pobj on ADP NOUN [sacred]
, punct identify VERB PUNCT []
the det deis NOUN DET []
the det deis NOUN DET []
deis nsubj identify VERB NOUN [the, the, for]
for prep deis NOUN ADP [mine]
the det mine NOUN DET []
mine pobj for ADP NOUN [the]
does aux identify VERB AUX []
not neg id

the det service NOUN DET []
forest compound service NOUN NOUN []
service nsubj ensure VERB NOUN [the, forest]
should aux ensure VERB AUX []
ensure ROOT ensure VERB VERB [service, should, used, .]
that mark used VERB SCONJ []
public amod lands NOUN ADJ []
lands nsubjpass used VERB NOUN [public]
are auxpass used VERB AUX []
not neg used VERB PART []
used ccomp ensure VERB VERB [that, lands, are, not, for]
for prep used VERB ADP [mt]
mining compound mt PROPN NOUN []
mt pobj for ADP PROPN [mining]
. punct ensure VERB PUNCT []
taylor compound   SPACE PROPN []
  dep   SPACE SPACE [taylor, sacred, .]
sacred amod   SPACE ADJ [to]
to prep sacred ADJ ADP [tribes]
native amod tribes NOUN ADJ []
tribes pobj to ADP NOUN [native, ,, precious]
, punct tribes NOUN PUNCT []
precious amod tribes NOUN ADJ [for, in]
for prep precious ADJ ADP [groundwater]
groundwater pobj for ADP NOUN []
in prep precious ADJ ADP [land]
an det land NOUN DET []
arid amod land NOUN ADJ []
land pobj in ADP NOUN [an, arid]
. p

i nsubj urge VERB PRON []
urge ROOT urge VERB VERB [i, you, select, .]
you dobj urge VERB PRON []
to aux select VERB PART []
select xcomp urge VERB VERB [to,  , in]
option compound   SPACE NOUN []
  dep select VERB SPACE [option]
in prep select VERB ADP [eis]
the det eis NOUN DET []
draft compound eis NOUN NOUN []
eis pobj in ADP NOUN [the, draft, prohibit]
which nsubj prohibit VERB PRON []
would aux prohibit VERB AUX []
prohibit relcl eis NOUN VERB [which, would, shafts]
mining compound shafts NOUN NOUN []
shafts dobj prohibit VERB NOUN [mining, on]
on prep shafts NOUN ADP [lands]
lands pobj on ADP NOUN [held]
held acl lands NOUN VERB [in]
in prep held VERB ADP [trust]
trust pobj in ADP NOUN [for]
for prep trust NOUN ADP [americans]
all det americans NOUN DET []
americans pobj for ADP NOUN [all, ,, present]
, punct americans NOUN PUNCT []
present amod americans NOUN ADJ [and, future]
and cc present ADJ CCONJ []
future conj present ADJ ADJ []
. punct urge VERB PUNCT []
in prep identify

KeyboardInterrupt: 

In [65]:
for sentence in tok_all:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      descriptive_term = token
  print(sentence)
  print(descriptive_term)

visiting from las vegas.

here for the mountain biking.

having the may valley trails as an option to ride in addition to the idyllwild trails was a perfect fit for my  day visit.
perfect
i would love to share these trails with all of my friends in las vegas.

please keep the current may valley trails open.
open
shastatrinity national forest httpwww.fs.usda.govstnf  i am a frequent user of the hurkey, may valley, and southridge area trails, and appreciate the value the nfs places on the trail system there, and the emphasis on legitimizing these truly amazing trails by affording them official nfs trail status.
official
that is great news i have read the may th usfs letter with proposed management and trail closures.
usfs
many of these proposed trail closures make some sense, but many do not.
many
some of the core mid may valley technical trails like log pile, uno and tres hombres, and secret being considered for closure are sacred trails to the mountain biking community in my opinion.
s

i hope to see these trails remain in the state they currently are in difficult, circuitious, challenging, humbling.
challenging
the midmay valley trails were not built for beginner riders.

many other trails exist in much closer proximity to existing trailheads and can be enjoyed by beginner and intermediate bike riders.
closer
but when they are ready for the challenge, i hope that the expert level trails in may valley will still be there to provide the challenges and rewards that i worked so hard to be able to enjoy and that all riders can strive to master
able
 httpwww.fs.usda.govstnf shastatrinity national forest please find attached my contribution to the public comment period for the may valley trails project.
public
 httpwww.fs.usda.govstnf shastatrinity national forest please find attached my contribution to the public comment period for the may valley trails project.
public
fw may valley non motorized trail project shastatrinity national forest httpwww.fs.usda.govstnf  subject 

trails need to be designed and managed so that they do not become motorized trails.
motorized
no extreme downhill trails which do not lend themselves to controlling erosion should be allowed.
extreme
all trails with significant erosion or other issues that cannot be controlled should be closed.
other
the final system needs to be manageable with current fs staff and volunteers.
current
please consider and use the analysis in the forest plan eis as part of your biological analysis.
biological
there was a lot of work on the mountain bike issue during the plan development.

please keep me informed for the rest of the process and make sure i am on the district list of interested persons for all nepa work.
interested
if there are any public fieldtrips or meetings with the users, please let me know so i can attend if possible.
possible
on thu, jun ,  at  pm, ladley, john c fs  wrote for information  scoping for may valley nonmotorized trails project closed june  tomorrow.

related docs can be

to provide an acceptable connection from trail a to rd s a	obtain a right of way or easement for a trail connector from a to s a road exists, though i am not aware if there are access issues through it.
aware
b	if public access through the public property cannot be achieve a singletrack could be built from a around the e boundary of the private property to connect from trail a to  which would provide a lower elevation link without having to climb all the way to may valley rd.
lower
a number of trail segments have been proposed for closure to which i object a	   .

these are tight, twisty turny trails which are sustainable as built minimal maintenance required since built and which provide significant variety, route options, and technical challenge to the may valley trail network.
technical
these trails are favorites of mountain bikers and fill a specific need with respect to technical challenge and diversity.
technical
i understand there is a concern on behalf of the forest service as 

there is no other areas around this area to ride trails like these.
other
there is currently many multi use trails for beginners in the area.
multi
most beginners or hikers or horse riders would go that far anyway.
most
but im for expanding the trail system but not closure of the proposed trails.

hello usfs, please accept this letter from idyllwild cycling and the international mountain bicycling association in response to the current may valley scoping document.
current
if you have questions, please feel free to contact katie hedrich at idyllwild cycling, as a board member and usfs liaison, or feel free to contact myself as imba regional director for the southwestern region.
southwestern
thanks for taking our comments on this project and for providing mountain bike access to public lands  much appreciated.
public
international mountain bicycling association june ,        mr. arturo delgado    district ranger    san jacinto ranger district    p.o.

box     idyllwild, ca        re  may

...

taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to communities along the route.
sacred
cumulative impacts, including health impacts, are not adequately addressed in the deis.
cumulative
we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico has a long legacy of uranium mining, much of which has not been cleaned up and continues to pollute people, land air and water.
much
foreign mining companies profits should not come at the expense of the people of new mexico, and all americans.
foreign
thank you for the opportunity to comment.

say no to roca honda mining on public lands the

new mexico is home to hundreds of abandoned uranium mines, with thousands more on the navajo nation.
navajo
these mines leak contaminants into groundwater, release radon into the air, and contribute to health problems of residents living in contaminated communities.

thousands of mine and mill workers have suffered, and continue to suffer and die, from working in hazardous conditions.
hazardous
while there have been some improvements in worker safety, there will always be risks associated with working in mines.

local communities deserve jobs without the thank you for considering my comments and i look forward to reviewing
local
say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust f

mining on mt taylor jeopardizes the spiritual harmony and balance of local communities.
local
historical and cultural impacts need to be analyzed under the protection of the national historic preservation roca honda proposes to open their mining operation with no plan on what to do with the uranium once it is mined.
historic
there is only one operating mill in the united states, which is not currently taking in any additional ore to process.
additional
the fact that there is nowhere to take and store the waste is a critical problem.
critical
it is irresponsible and dangerous to begin mining when there is no answer for waste disposal.
dangerous
roca honda would transport radioactive and hazardous materials through surrounding communities.
hazardous
local law enforcement and public health entities are not prepared to handle accidents during transport.
prepared
communities would bear the brunt of responding to emergency situations and living with the aftermath.

the deis does not identify

thank you for the opportunity to comment.

say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to communities along the route.
sacred
cumulative impacts, including health impacts, are not adequately addressed in the deis.
cumulative
we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico has a long legacy of uranium mining, much of which has not been cleaned up and continues to pollute people, land air and w

the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to communities along the route.
sacred
cumulative impacts, including health impacts, are not adequately addressed in the deis.
cumulative
we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico has a long legacy of uranium mining, much of which has not been cleaned up and continues to pollute people, land air and water.
much
foreign mining companies profits should not come at the expense of the people of new mexico, and all americans.
foreign
when

In [66]:
for sentence in tok_all:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  print(sentence)
  print(descriptive_term)

visiting from las vegas.

here for the mountain biking.

having the may valley trails as an option to ride in addition to the idyllwild trails was a perfect fit for my  day visit.
perfect
i would love to share these trails with all of my friends in las vegas.

please keep the current may valley trails open.
open
shastatrinity national forest httpwww.fs.usda.govstnf  i am a frequent user of the hurkey, may valley, and southridge area trails, and appreciate the value the nfs places on the trail system there, and the emphasis on legitimizing these truly amazing trails by affording them official nfs trail status.
official
that is great news i have read the may th usfs letter with proposed management and trail closures.
usfs
many of these proposed trail closures make some sense, but many do not.
many
some of the core mid may valley technical trails like log pile, uno and tres hombres, and secret being considered for closure are sacred trails to the mountain biking community in my opinion.
s

but when they are ready for the challenge, i hope that the expert level trails in may valley will still be there to provide the challenges and rewards that i worked so hard to be able to enjoy and that all riders can strive to master
able
 httpwww.fs.usda.govstnf shastatrinity national forest please find attached my contribution to the public comment period for the may valley trails project.
public
 httpwww.fs.usda.govstnf shastatrinity national forest please find attached my contribution to the public comment period for the may valley trails project.
public
fw may valley non motorized trail project shastatrinity national forest httpwww.fs.usda.govstnf  subject may valley non motorized trail project i wrote a letter to you the other day commenting on this project, wanted to add more.
more
everybody talks about economic impact that the cyclists bring, but nobody really has any numbers in this mornings imperial valley press, there were numbers for the imperial sand dunes which i thought 

criteria can be set at the beginning that can be used by yearly evaluations to determine the degree of success in sustainability for each section of the trail system.
yearly
the decision to maintain or alter can trails can be determined with each evaluation.

it obviously will then be incumbent on the trail users to organize, plan and direct trail maintenance activities in order to keep the system ontrack.
direct
i think this will work in the may valley system just as it has in other trail systems in the united states.
other
i join other members of the trail using community to request that the may valley trail system be preserved.
other
i, as many others, pledge to continue support by both physically working to maintain trails and contribute to public comment such as this.
such
thank you for your thoughtful comments.
thoughtful
i am sorry about the short turnaround time.
short
your comments will be included in the project record.

supervisory natural resources specialist subject re may

big picture dreaming i would love to see newly built singletrack to achieve the following loops and connections in the may valley area a	a singletrack loop trail connecting the following south end of may valley down to morris ranch road across the valley to the bottom of thomas mountain climb up and over the ridge across thomas mtn rd to the west side north along backside of thomas mtn to rouse ridge climb up and cross hwy  connect around to trails in alvin meadowshub trails connect back to idyllwild south around private property to may valley rd which then ties back into the may valley trail system.
private
b	from the above mentioned loop, a trail down towards anza which could connect to coyote canyon in anza borrego desert state park.
above
c	  singletrack connecting down into hemet d	singletrack which connects from hurkey creek to morris ranch rd, south around to palm canyon and santa rosa mountain.

there are existing roads which are likely now very primitive which could provide pa

bringing enhanced mountain biking opport unities to the town would  increase the overall tourism  numbers  and would aid greatly to the economy.
overall
the  mountain bike experience is dependent on the quality and sust ainability of trails and a  well    planned system will make idyllwild a desirable mountain bi king destination.
desirable
the number of trails will have a direct impact on the experience users will have in the  new system.
new
each trail has its own personality because of the unique topography of the  area.
unique
a trail in a stacked system isnt so much about gett ing to point a to point b.     it is  about the opportunity to create different experiences time and time again in a smaller, well    planned area.
smaller
trails may seem to be in close proximity but on the ground they are  not visible to one another and allow for multi ple loops varying in length and  ability  level.
visible
we are in agreement with the forest service about the existing trails they have  c

...

say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to communities along the route.
sacred
cumulative impacts, including health impacts, are not adequately addressed in the deis.
cumulative
we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico has a long legacy of uranium mining, much of which has not been cleaned up and continues to pollute people, land air and water.
much
foreign mining companies profits

insitu leach mining involves purposefully contaminating groundwater to mobilize uranium.
insitu
roca honda would be a conventional underground mine, the same type of mines that new mexico state and federal agencies are not taking into account other nearby mining projects and the cumulative impacts these mines would have on health, water and other natural resources near mt taylor.
natural
the section on cumulative impacts lists other projects in the grants mining district, but doesnt provide a map showing their location or what communities in northwestern nm are living with the contamination of the past.
northwestern
families living nearby abandoned uranium mines and mills notice increased rates of cancers and other health problems.
other
this problem has been ignored by state and federal agencies.
federal
to proceed with more mines without knowing the scope of impact to peoples health is dangerous and the federal government and the state of new mexico need to recognize the rights of pe

we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico has a long legacy of uranium mining, much of which has not been cleaned up and continues to pollute people, land air and water.
much
foreign mining companies profits should not come at the expense of the people of new mexico, and all americans.
foreign
thank you for the opportunity to comment.

say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to comm

foreign mining companies profits should not come at the expense of the people of new mexico, and all americans.
foreign
thank you for the opportunity to comment.

say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust for all americans, present and future.
future
in addition to encroaching on sacred lands, the the deis for the mine does not identify a mill site or the transportation route for the uranium ore, which could have impacts to communities along the route.
sacred
cumulative impacts, including health impacts, are not adequately addressed in the deis.
cumulative
we know that uranium mining can harm health and can also have serious impacts on air and water.
serious
new mexico ha

new mexico is home to hundreds of abandoned uranium mines, with thousands more on the navajo nation.
navajo
these mines leak contaminants into groundwater, release radon into the air, and contribute to health problems of residents living in contaminated communities.

thousands of mine and mill workers have suffered, and continue to suffer and die, from working in hazardous conditions.
hazardous
while there have been some improvements in worker safety, there will always be risks associated with working in mines.

local communities deserve jobs without the thank you for considering my comments and i look forward to reviewing
local
say no to roca honda mining on public lands the roca honda mine should not be built.
public
the forest service should ensure that public lands are not used for mining mt.
public
taylor  sacred to native tribes, precious for groundwater in an arid land.
arid
i urge you to select option  in the draft eis which would prohibit mining shafts on lands held in trust f

In [68]:
aspects = []
for sentence in tok_all:
  doc = nlp(sentence)
  descriptive_term = ''
  target = ''
  for token in doc:
    if token.dep_ == 'nsubj' and token.pos_ == 'NOUN':
      target = token.text
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  aspects.append({'aspect': target,
    'description': descriptive_term})
print(aspects)

[{'aspect': '', 'description': ''}, {'aspect': '', 'description': ''}, {'aspect': '', 'description': 'perfect'}, {'aspect': '', 'description': ''}, {'aspect': '', 'description': 'open'}, {'aspect': 'forest', 'description': 'official'}, {'aspect': '', 'description': 'usfs'}, {'aspect': '', 'description': 'many'}, {'aspect': '', 'description': 'sacred'}, {'aspect': '', 'description': ''}, {'aspect': 'pile', 'description': 'huge'}, {'aspect': '', 'description': 'huge'}, {'aspect': 'section', 'description': 'pine'}, {'aspect': '', 'description': 'sure'}, {'aspect': 'trail', 'description': 'hard'}, {'aspect': '', 'description': 'obvious'}, {'aspect': '', 'description': ''}, {'aspect': '', 'description': 'crazy'}, {'aspect': '', 'description': 'secret'}, {'aspect': 'trail', 'description': 'challenging'}, {'aspect': 'reason', 'description': 'technical'}, {'aspect': 'trails', 'description': 'technical'}, {'aspect': 'signage', 'description': 'acceptable'}, {'aspect': 'trails', 'description': 'c

In [69]:
from textblob import TextBlob
for aspect in aspects:
  aspect['sentiment'] = TextBlob(aspect['description']).sentiment
print(aspects)

[{'aspect': '', 'description': '', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': '', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': 'perfect', 'sentiment': Sentiment(polarity=1.0, subjectivity=1.0)}, {'aspect': '', 'description': '', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': 'open', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.5)}, {'aspect': 'forest', 'description': 'official', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': 'usfs', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': 'many', 'sentiment': Sentiment(polarity=0.5, subjectivity=0.5)}, {'aspect': '', 'description': 'sacred', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': '', 'description': '', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': 'pile', 'description': 'huge', 'sentime

In [89]:
aspects


[{'aspect': '',
  'description': '',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': '',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': 'perfect',
  'sentiment': Sentiment(polarity=1.0, subjectivity=1.0)},
 {'aspect': '',
  'description': '',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': 'open',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.5)},
 {'aspect': 'forest',
  'description': 'official',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': 'usfs',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': 'many',
  'sentiment': Sentiment(polarity=0.5, subjectivity=0.5)},
 {'aspect': '',
  'description': 'sacred',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 {'aspect': '',
  'description': '',
  'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)},
 

In [91]:
tok_all

['visiting from las vegas.',
 'here for the mountain biking.',
 'having the may valley trails as an option to ride in addition to the idyllwild trails was a perfect fit for my  day visit.',
 'i would love to share these trails with all of my friends in las vegas.',
 'please keep the current may valley trails open.',
 'shastatrinity national forest httpwww.fs.usda.govstnf  i am a frequent user of the hurkey, may valley, and southridge area trails, and appreciate the value the nfs places on the trail system there, and the emphasis on legitimizing these truly amazing trails by affording them official nfs trail status.',
 'that is great news i have read the may th usfs letter with proposed management and trail closures.',
 'many of these proposed trail closures make some sense, but many do not.',
 'some of the core mid may valley technical trails like log pile, uno and tres hombres, and secret being considered for closure are sacred trails to the mountain biking community in my opinion.',


In [90]:
from textblob.classifiers import NaiveBayesClassifier
# We train the NaivesBayesClassifier
train = [
  ('bad plan.', 'negative'),
  ('great trail.', 'positive'),
  ('harmful policy.', 'negative'),
  ('very enjoyable visit.', 'positive'),
  ('worse idea.', 'negative')
]

cl = NaiveBayesClassifier(train)
# And then we try to classify some sample sentences.
blob = TextBlob(tok_all,classifier = cl)
#blob = TextBlob("Delicious food. Very Slow internet. Suboptimal experience. Enjoyable visit.", classifier=cl)
for s in blob.sentences:
  print(s)
  print(s.classify())

TypeError: The `text` argument passed to `__init__(text)` must be a string, not <class 'list'>

In [35]:
stop_words = stopwords.words('english')
from stop_words import get_stop_words
stop_words2 = get_stop_words('en')
stop_words.extend(stop_words2) 

# remove stopwords

df2['remove_stopwords'] = df2['tokenise'].apply(lambda x: [item for item in x if item not in stop_words])

display(df2.head(10))

/var/folders/n_/4b1w6nqd5gdgtmmlrm6pm82c0000gn/T/ipykernel_59965/4032015913.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df2['remove_stopwords'] = df2['tokenise'].apply(lambda x: [item for item in x if item not in stop_words])


Letter.Text.Clean  \
0  visiting from las vegas.  here for the mountai...   
1  shastatrinity national forest httpwww.fs.usda....   
2  shastatrinity national forest httpwww.fs.usda....   
3  shastatrinity national forest httpwww.fs.usda....   
4   httpwww.fs.usda.govstnf shastatrinity nationa...   
5   httpwww.fs.usda.govstnf shastatrinity nationa...   
6  fw may valley non motorized trail project shas...   
7  supervisory natural resources specialist about...   
8  shastatrinity national forest httpwww.fs.usda....   
9  fw public comment may valley trails system  ht...   

                                            tokenise  \
0  [visiting, from, las, vegas, ., here, for, the...   
1  [shastatrinity, national, forest, httpwww.fs.u...   
2  [shastatrinity, national, forest, httpwww.fs.u...   
3  [shastatrinity, national, forest, httpwww.fs.u...   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
6  [fw, may, valley, non, motorized, trail, proje...   
7  [supervisory, natural, resources, specialist, ...   
8  [shastatrinity, national, forest, httpwww.fs.u...   
9  [fw, public, comment, may, valley, trails, sys...   

                                    remove_stopwords  
0  [visiting, las, vegas, ., mountain, biking, .,...  
1  [shastatrinity, national, forest, httpwww.fs.u...  
2  [shastatrinity, national, forest, httpwww.fs.u...  
3  [shastatrinity, national, forest, httpwww.fs.u...  
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...  
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...  
6  [fw, may, valley, non, motorized, trail, proje...  
7  [supervisory, natural, resources, specialist, ...  
8  [shastatrinity, national, forest, httpwww.fs.u...  
9  [fw, public, comment, may, valley, trails, sys...

In [36]:
# initiate nltk lemmatiser

wordnet_lemmatizer = WordNetLemmatizer()

# lemmatise words

df2['lemmatise'] = df2['remove_stopwords'].apply(lambda x: [wordnet_lemmatizer.lemmatize(y) for y in x]) 

display(df2.head(10))


Letter.Text.Clean  \
0  visiting from las vegas.  here for the mountai...   
1  shastatrinity national forest httpwww.fs.usda....   
2  shastatrinity national forest httpwww.fs.usda....   
3  shastatrinity national forest httpwww.fs.usda....   
4   httpwww.fs.usda.govstnf shastatrinity nationa...   
5   httpwww.fs.usda.govstnf shastatrinity nationa...   
6  fw may valley non motorized trail project shas...   
7  supervisory natural resources specialist about...   
8  shastatrinity national forest httpwww.fs.usda....   
9  fw public comment may valley trails system  ht...   

                                            tokenise  \
0  [visiting, from, las, vegas, ., here, for, the...   
1  [shastatrinity, national, forest, httpwww.fs.u...   
2  [shastatrinity, national, forest, httpwww.fs.u...   
3  [shastatrinity, national, forest, httpwww.fs.u...   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
6  [fw, may, valley, non, motorized, trail, proje...   
7  [supervisory, natural, resources, specialist, ...   
8  [shastatrinity, national, forest, httpwww.fs.u...   
9  [fw, public, comment, may, valley, trails, sys...   

                                    remove_stopwords  \
0  [visiting, las, vegas, ., mountain, biking, .,...   
1  [shastatrinity, national, forest, httpwww.fs.u...   
2  [shastatrinity, national, forest, httpwww.fs.u...   
3  [shastatrinity, national, forest, httpwww.fs.u...   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
6  [fw, may, valley, non, motorized, trail, proje...   
7  [supervisory, natural, resources, specialist, ...   
8  [shastatrinity, national, forest, httpwww.fs.u...   
9  [fw, public, comment, may, valley, trails, sys...   

                                           lemmatise  
0  [visiting, la, vega, ., mountain, biking, ., m...  
1  [shastatrinity, national, forest, httpwww.fs.u...  
2  [shastatrinity, national, forest, httpwww.fs.u...  
3  [shastatrinity, national, forest, httpwww.fs.u...  
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...  
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...  
6  [fw, may, valley, non, motorized, trail, proje...  
7  [supervisory, natural, resource, specialist, t...  
8  [shastatrinity, national, forest, httpwww.fs.u...  
9  [fw, public, comment, may, valley, trail, syst...

In [38]:
# initialise the count vectorizer

vectorizer = CountVectorizer(analyzer = 'word', ngram_range = (2, 2))
                            
# join the processed data to be vectorised

vectors = []

for index, row in df2.iterrows():
    vectors.append(", ".join(row[3]))

vectorised = vectorizer.fit_transform(vectors)

print(vectorised)

  (0, 20170)	1
  (0, 9379)	2
  (0, 20087)	1
  (0, 11750)	1
  (0, 1945)	1
  (0, 10728)	2
  (0, 20019)	2
  (0, 19154)	1
  (0, 12934)	1
  (0, 15953)	1
  (0, 289)	1
  (0, 8327)	1
  (0, 19157)	1
  (0, 13432)	1
  (0, 6590)	1
  (0, 4220)	1
  (0, 20160)	1
  (0, 10290)	1
  (0, 16897)	1
  (0, 19091)	1
  (0, 6857)	1
  (0, 20088)	1
  (0, 13801)	1
  (0, 9242)	1
  (0, 4051)	1
  :	:
  (4999, 18705)	1
  (4999, 11172)	1
  (4999, 20981)	1
  (4999, 17946)	1
  (4999, 3640)	1
  (4999, 17938)	1
  (4999, 4740)	1
  (4999, 20992)	1
  (4999, 7675)	1
  (4999, 3276)	1
  (4999, 8580)	1
  (4999, 20978)	1
  (4999, 16337)	1
  (4999, 821)	1
  (4999, 16063)	1
  (4999, 1430)	1
  (4999, 20994)	1
  (4999, 11282)	1
  (4999, 3013)	1
  (4999, 4531)	1
  (4999, 9154)	1
  (4999, 20896)	1
  (4999, 18549)	1
  (4999, 3472)	1
  (4999, 6790)	1


In [39]:
# initisalise LDA Model

lda_model = LatentDirichletAllocation(n_components = 5, # number of topics
                                  random_state = 10,          # random state
                                  evaluate_every = -1,      # compute perplexity every n iters, default: Don't
                                  n_jobs = -1,              # Use all available CPUs
                                 )

lda_output = lda_model.fit_transform(vectorised)

# column names

topic_names = ["Topic" + str(i) for i in range(1, lda_model.n_components + 1)]

# make the pandas dataframe

df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns = topic_names)

# get dominant topic for each document

dominant_topic = (np.argmax(df_document_topic.values, axis=1)+1)
df_document_topic['Dominant_topic'] = dominant_topic

# join to original dataframes

df2 = pd.merge(df2, df_document_topic, left_index = True, right_index = True, how = 'outer')
display(df2.head(10))

Letter.Text.Clean  \
0  visiting from las vegas.  here for the mountai...   
1  shastatrinity national forest httpwww.fs.usda....   
2  shastatrinity national forest httpwww.fs.usda....   
3  shastatrinity national forest httpwww.fs.usda....   
4   httpwww.fs.usda.govstnf shastatrinity nationa...   
5   httpwww.fs.usda.govstnf shastatrinity nationa...   
6  fw may valley non motorized trail project shas...   
7  supervisory natural resources specialist about...   
8  shastatrinity national forest httpwww.fs.usda....   
9  fw public comment may valley trails system  ht...   

                                            tokenise  \
0  [visiting, from, las, vegas, ., here, for, the...   
1  [shastatrinity, national, forest, httpwww.fs.u...   
2  [shastatrinity, national, forest, httpwww.fs.u...   
3  [shastatrinity, national, forest, httpwww.fs.u...   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
6  [fw, may, valley, non, motorized, trail, proje...   
7  [supervisory, natural, resources, specialist, ...   
8  [shastatrinity, national, forest, httpwww.fs.u...   
9  [fw, public, comment, may, valley, trails, sys...   

                                    remove_stopwords  \
0  [visiting, las, vegas, ., mountain, biking, .,...   
1  [shastatrinity, national, forest, httpwww.fs.u...   
2  [shastatrinity, national, forest, httpwww.fs.u...   
3  [shastatrinity, national, forest, httpwww.fs.u...   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...   
6  [fw, may, valley, non, motorized, trail, proje...   
7  [supervisory, natural, resources, specialist, ...   
8  [shastatrinity, national, forest, httpwww.fs.u...   
9  [fw, public, comment, may, valley, trails, sys...   

                                           lemmatise  Topic1  Topic2  Topic3  \
0  [visiting, la, vega, ., mountain, biking, ., m...    0.01    0.01    0.01   
1  [shastatrinity, national, forest, httpwww.fs.u...    0.00    0.00    0.00   
2  [shastatrinity, national, forest, httpwww.fs.u...    0.00    0.00    0.00   
3  [shastatrinity, national, forest, httpwww.fs.u...    0.00    0.79    0.00   
4  [httpwww.fs.usda.govstnf, shastatrinity, natio...    0.01    0.01    0.16   
5  [httpwww.fs.usda.govstnf, shastatrinity, natio...    0.01    0.01    0.16   
6  [fw, may, valley, non, motorized, trail, proje...    0.00    0.00    0.00   
7  [supervisory, natural, resource, specialist, t...    0.00    0.00    0.99   
8  [shastatrinity, national, forest, httpwww.fs.u...    0.00    0.00    0.00   
9  [fw, public, comment, may, valley, trail, syst...    0.00    0.00    0.00   

   Topic4  Topic5  Dominant_topic  
0    0.01    0.97             5.0  
1    0.00    1.00             5.0  
2    0.00    1.00             5.0  
3    0.00    0.21             2.0  
4    0.01    0.80             5.0  
5    0.01    0.80             5.0  
6    0.00    1.00             5.0  
7    0.00    0.00             3.0  
8    0.00    0.99             5.0  
9    0.00    1.00             5.0

Project.Number  FOREST_ID  Letter.Number Author.ZipCode sentiment  \
0              15568      512.0             19            NaN  Positive   
1              15568      512.0             39            NaN  Positive   
2              15568      512.0             59            NaN  Positive   
3              15568      512.0              4            NaN  Positive   
4              15568      512.0             11            NaN  Positive   
...              ...        ...            ...            ...       ...   
4995           18431      303.0           3836            NaN  Positive   
4996           18431      303.0           3837            NaN  Negative   
4997           18431      303.0           3838            NaN  Negative   
4998           18431      303.0           3839            NaN  Negative   
4999           18431      303.0            384            NaN  Negative   

      sentiment score  
0              0.9403  
1              0.9992  
2              0.9619  
3              0.9929  
4              0.3182  
...               ...  
4995           0.7184  
4996          -0.9929  
4997          -0.9929  
4998          -0.9929  
4999          -0.9929  

[5000 rows x 6 columns]

In [49]:
# index names
docnames = ['Doc' + str(i) for i in range(len(df_meta))]

# Make the pandas dataframe
df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topic_names, index=docnames)

# Get dominant topic for each document
dominant_topic = np.argmax(df_document_topic.values, axis=1)
df_document_topic['dominant_topic'] = dominant_topic

# Topic-Keyword Matrix
df_topic_keywords = pd.DataFrame(lda_model.components_)

# Assign Column and Index
df_topic_keywords.columns = vectorizer.get_feature_names()
df_topic_keywords.index = topic_names

df_topic_no = pd.DataFrame(df_topic_keywords.idxmax())
df_scores = pd.DataFrame(df_topic_keywords.max())

tmp = pd.merge(df_topic_no, df_scores, left_index=True, right_index=True)
tmp.columns = ['topic', 'relevance_score']

display(tmp)

topic  relevance_score
aaron department      Topic5         1.199840
abandon dangerous     Topic5         1.199916
abandoned mine        Topic5         3.199511
abandoned uranium     Topic2      2875.738391
abandonment property  Topic5         1.199840
...                      ...              ...
zuni comment          Topic3         1.199988
zuni mine             Topic5         1.198218
zuni new              Topic5         1.199996
zuni response         Topic3         1.199988
zuni valued           Topic3         2.199894

[21211 rows x 2 columns]

In [ ]:
all_topics = []

tmp_1 = tmp.loc[tmp['topic'] == i].reset_index()
    tmp_1 = tmp_1.sort_values('relevance_score', ascending=False).head(1)

    tmp_1['topic'] = tmp_1['topic'] + 1
    
    tmp_2 = []
    tmp_2.append(tmp_1['topic'].unique()[0])
    tmp_2.append(list(tmp_1['index'].unique()))
    all_topics.append(tmp_2)

all_topics = pd.DataFrame(all_topics, columns=['Dominant_topic', 'topic_name'])
display(all_topics)

In [51]:
all_topics = []

for i in tmp['topic'].unique():    
    tmp_1 = tmp.loc[tmp['topic'] == i].reset_index()
    tmp_1 = tmp_1.sort_values('relevance_score', ascending=False).head(1)

    tmp_1['topic'] = tmp_1['topic'] + 1
    
    tmp_2 = []
    tmp_2.append(tmp_1['topic'].unique()[0])
    tmp_2.append(list(tmp_1['index'].unique()))
    all_topics.append(tmp_2)

all_topics = pd.DataFrame(all_topics, columns=['Dominant_topic', 'topic_name'])
display(all_topics)

TypeError: can only concatenate str (not "int") to str

In [2]:
for sentence in sentences:
  doc = nlp(sentence)
  for token in doc:
    print(token.text, token.dep_, token.head.text, token.head.pos_,
      token.pos_,[child for child in token.children])


The det food NOUN DET []
food nsubj was AUX NOUN [The, had]
we nsubj had AUX PRON []
had relcl food NOUN AUX [we, yesterday]
yesterday npadvmod had AUX NOUN []
was ROOT was AUX AUX [food, delicious]
delicious acomp was AUX ADJ []
My poss time NOUN DET []
time nsubj was AUX NOUN [My, in]
in prep time NOUN ADP [Italy]
Italy pobj in ADP PROPN []
was ROOT was AUX AUX [time, enjoyable]
very advmod enjoyable ADJ ADV []
enjoyable acomp was AUX ADJ [very]
I nsubj found VERB PRON []
found ROOT found VERB VERB [I, be]
the det meal NOUN DET []
meal nsubj be AUX NOUN [the]
to aux be AUX PART []
be ccomp found VERB AUX [meal, to, tasty]
tasty acomp be AUX ADJ []
The det internet NOUN DET []
internet nsubj was AUX NOUN [The]
was ROOT was AUX AUX [internet, slow, .]
slow acomp was AUX ADJ []
. punct was AUX PUNCT []
Our poss experience NOUN DET []
experience nsubj was AUX NOUN [Our]
was ROOT was AUX AUX [experience, suboptimal]
suboptimal acomp was AUX ADJ []


In [19]:
for sentence in sentences:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      descriptive_term = token
  print(sentence)
  print(descriptive_term)

The food we had yesterday was delicious
delicious
My time in Italy was very enjoyable
enjoyable
I found the meal to be tasty
tasty
The internet was slow.
slow
Our experience was suboptimal
suboptimal


In [20]:
for sentence in sentences:
  doc = nlp(sentence)
  descriptive_term = ''
  for token in doc:
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  print(sentence)
  print(descriptive_term)

The food we had yesterday was delicious
delicious
My time in Italy was very enjoyable
very enjoyable
I found the meal to be tasty
tasty
The internet was slow.
slow
Our experience was suboptimal
suboptimal


In [21]:
aspects = []
for sentence in sentences:
  doc = nlp(sentence)
  descriptive_term = ''
  target = ''
  for token in doc:
    if token.dep_ == 'nsubj' and token.pos_ == 'NOUN':
      target = token.text
    if token.pos_ == 'ADJ':
      prepend = ''
      for child in token.children:
        if child.pos_ != 'ADV':
          continue
        prepend += child.text + ' '
      descriptive_term = prepend + token.text
  aspects.append({'aspect': target,
    'description': descriptive_term})
print(aspects)


[{'aspect': 'food', 'description': 'delicious'}, {'aspect': 'time', 'description': 'very enjoyable'}, {'aspect': 'meal', 'description': 'tasty'}, {'aspect': 'internet', 'description': 'slow'}, {'aspect': 'experience', 'description': 'suboptimal'}]


In [23]:
#https://textblob.readthedocs.io/en/dev/install.html


In [22]:
from textblob import TextBlob
for aspect in aspects:
  aspect['sentiment'] = TextBlob(aspect['description']).sentiment
print(aspects)

[{'aspect': 'food', 'description': 'delicious', 'sentiment': Sentiment(polarity=1.0, subjectivity=1.0)}, {'aspect': 'time', 'description': 'very enjoyable', 'sentiment': Sentiment(polarity=0.65, subjectivity=0.78)}, {'aspect': 'meal', 'description': 'tasty', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}, {'aspect': 'internet', 'description': 'slow', 'sentiment': Sentiment(polarity=-0.30000000000000004, subjectivity=0.39999999999999997)}, {'aspect': 'experience', 'description': 'suboptimal', 'sentiment': Sentiment(polarity=0.0, subjectivity=0.0)}]


In [ ]:
### from the example. ### who to keep training the classifier
#python -m textblob.download_corpora
#from textblob.classifiers import NaiveBayesClassifier
# We train the NaivesBayesClassifier
#train = [
#  ('Slow internet.', 'negative'),
#  ('Delicious food', 'positive'),
#  ('Suboptimal experience', 'negative'),
#  ('Very enjoyable time', 'positive'),
#  ('delicious food.', 'neg')
#]
#cl = NaiveBayesClassifier(train)
# And then we try to classify some sample sentences.
#blob = TextBlob("Delicious food. Very Slow internet. Suboptimal experience. Enjoyable food.", classifier=cl)
#for s in blob.sentences:
#  print(s)
#  print(s.classify())
    
